# Plot the Near-Inertial Activity Forecast

To see how we got here, check the notebooks
- [loading the data](./01_download_GFS_data.ipynb)
- and [running the slab-ocean model](./02_run_slab_model.ipynb).

## Parameters

In [1]:
# parameters

GFS_zarr_store = "tmp_GFS.zarr"
slab_zarr_store = "tmp_slab.zarr"

dask_kwargs = {"n_workers": 1, "threads_per_worker": 4, "memory_limit": 6e9}

## Tech preamble

Import modules and spin up Dask cluster.

In [2]:
import xarray as xr
from dask.distributed import Client
import hvplot.xarray

The memory requirements of the integration are currently relatively high. So we'll go for one single-threaded Worker with enough memory.

If we'll do this with Github Actions, there will be a total of [6GB memory](https://docs.github.com/en/actions/reference/virtual-environments-for-github-hosted-runners#supported-runners-and-hardware-resources) for all we do. So let's stay below this even in development.

In [3]:
client = Client(**dask_kwargs)
client

<Client: 'tcp://127.0.0.1:40857' processes=1 threads=4, memory=6.00 GB>

## Loading the data

In [4]:
ds_GFS = xr.open_zarr(GFS_zarr_store)
ds_slab = xr.open_zarr(slab_zarr_store)

In [5]:
import holoviews as hv

In [6]:
start_of_forecast = (~ds_GFS["is_forecast"].astype(bool)).isel(lat=0, lon=0, drop=True).sum().compute().data
start_of_forecast = ds_GFS["time"].data[start_of_forecast]

In [7]:
(
    hv.VLine(start_of_forecast)
    * ds_GFS["taux"].sel(lon=360-23, lat=12, method="nearest").hvplot.line(label="taux")
    * ds_GFS["tauy"].sel(lon=360-23, lat=12, method="nearest").hvplot.line(label="tauy")
    + hv.VLine(start_of_forecast)
    * ds_slab["u_slab"].sel(lon=360-23, lat=12, method="nearest").hvplot.line(label="u")
    * ds_slab["v_slab"].sel(lon=360-23, lat=12, method="nearest").hvplot.line(label="v")
    * ds_slab["umag_slab"].sel(lon=360-23, lat=12, method="nearest").hvplot.line(label="umag")
).cols(1)

:Layout
   .Overlay.I  :Overlay
      .VLine.I    :VLine   [x,y]
      .Curve.Taux :Curve   [time]   (taux)
      .Curve.Tauy :Curve   [time]   (tauy)
   .Overlay.II :Overlay
      .VLine.I    :VLine   [x,y]
      .Curve.U    :Curve   [time]   (u_slab)
      .Curve.V    :Curve   [time]   (v_slab)
      .Curve.Umag :Curve   [time]   (umag_slab)

In [8]:
import numpy as np

In [9]:
ds_slab["umag_slab"].max(
    "time"
).hvplot.contourf(
    levels=list(np.linspace(0, 2, 20))
)

:Polygons   [lon,lat]   (umag_slab)